<a href="https://colab.research.google.com/github/THANTANIN/long/blob/main/3c_BERT_finetuning_for_token_classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## State Condition

In [1]:
target = "status"
model_checkpoint = "airesearch/wangchanberta-base-att-spm-uncased"
batch_size = 16
num_epoch = 1
condition = f"pretokenized_conn_status"
limit_n_tokens = 200
save="epoch"
#save=("no","epoch", or "step")

In [2]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

/bin/bash: line 1: nvidia-smi: command not found


## Set Environment

In [3]:
!pip install datasets transformers seqeval
!pip install sentencepiece accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 1.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 14.5 MB/s eta 0:00:00
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16161 sha256=edb60f7372d851afce4e59133626dad6f78bdbed82ae49f65e2828614d51e84e
  Stored in directory: /root/.cache/pip/wheels/bc/92/f0/243288f899c2eacdfa8c5f9aede4c71a9bad0ee26a01dc5ead
Successfully built seqeval
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency re

In [4]:
! pip install evaluate

from evaluate import load


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 3.5 MB/s eta 0:00:00


In [5]:
import pandas as pd
import numpy as np
import glob
import sys
import os
import re

from transformers import (
    AutoModel, AutoTokenizer, AutoConfig,
    AutoModelForTokenClassification,
    TrainingArguments, Trainer,
    DataCollatorForTokenClassification
)

from datasets import (
    load_dataset,
    Dataset,
    DatasetDict,
    Features, Sequence, ClassLabel, Value
)
from sklearn.metrics import classification_report

In [6]:
lm_name = 'airesearch/wangchanberta-base-att-spm-uncased'
model = AutoModel.from_pretrained(lm_name)
tokenizer = AutoTokenizer.from_pretrained(lm_name)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/546 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/423M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/282 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/905k [00:00<?, ?B/s]

## Loading the dataset

In [7]:
from datasets import load_dataset
import pandas as pd

def get_df_from_huggingface(dataset_name, split="train", num_sent=1):
    """
    Convert a dataset from load_dataset to a DataFrame.

    Parameters
    ----------
    dataset_name : str
        Name of the dataset to load.
    split : str
        The dataset split to use ("train", "test", "validation").
    num_sent : int
        Number of sentences per row (default is 1 sentence per row).

    Returns
    -------
    pd.DataFrame
        DataFrame with processed data.
    """
    dataset = load_dataset(dataset_name, split=split)

    data = {"tokens": [], "conn_label": []}
    for entry in dataset:
        sentences = entry["summary"].split("\n")  # Example: Split text into sentences
        count_sent = 0
        column1, column2 = [], []

        for sentence in sentences:
            count_sent += 1
            column1.append(sentence.strip())  # Remove leading/trailing spaces
            column2.append("SP")  # Assign default label or adjust as needed

            if count_sent == num_sent:
                data["tokens"].append(column1)
                data["conn_label"].append(column2)
                column1, column2 = [], []
                count_sent = 0

        # Add remaining sentences if any
        if column1:
            data["tokens"].append(column1)
            data["conn_label"].append(column2)

    df = pd.DataFrame.from_dict(data)
    df["n_tokens"] = df.tokens.apply(len)
    return df

# Example usage:


In [8]:
train_df = get_df_from_huggingface("pythainlp/thaisum", split="train", num_sent=1)
test_df = get_df_from_huggingface("pythainlp/thaisum", split="test", num_sent=1)
dev_df = get_df_from_huggingface("pythainlp/thaisum", split="validation", num_sent=1)


README.md:   0%|          | 0.00/13.5k [00:00<?, ?B/s]

(…)-00000-of-00006-6e20f63d89ca77c0.parquet:   0%|          | 0.00/194M [00:00<?, ?B/s]

(…)-00001-of-00006-9989c60d1f9140e4.parquet:   0%|          | 0.00/194M [00:00<?, ?B/s]

(…)-00002-of-00006-d228c68dd60b0513.parquet:   0%|          | 0.00/193M [00:00<?, ?B/s]

(…)-00003-of-00006-d0c1675c6a75d466.parquet:   0%|          | 0.00/193M [00:00<?, ?B/s]

...

(…)-00000-of-00001-f0463a2623057daa.parquet:   0%|          | 0.00/46.3M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/358868 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/11000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11000 [00:00<?, ? examples/s]

Generating valid split:   0%|          | 0/11000 [00:00<?, ? examples/s]

In [9]:
display(train_df["tokens"][50])

['เบตง ตชด.445 ร่วม ตร.มาเลเซีย จับตัวชาวมาเลเซีย หนีคดีลักทรัพย์มูลค่ากว่า10 ล้านบาท มาซ่อนตัวที่ อ.เบตง ส่งตัวกลับไปดำเนินคดี']

In [10]:
train_df.describe()

n_tokens
count  370137.0
mean        1.0
std         0.0
min         1.0
25%         1.0
50%         1.0
75%         1.0
max         1.0

In [11]:
print(train_df , test_df.shape , dev_df.shape)
train_df = train_df[train_df.n_tokens<limit_n_tokens]
test_df = test_df[test_df.n_tokens<limit_n_tokens]
dev_df = dev_df[dev_df.n_tokens<limit_n_tokens]
print(train_df.shape , test_df.shape , dev_df.shape)

                                                   tokens conn_label  n_tokens
0       [วิษณุ ยันโรดแม็ปตามขั้นตอนเดิม เชื่อ สนช.หยุด...       [SP]         1
1       [รอกันมา 2 สัปดาห์ บอลสโมสรลีกต่างๆของยุโรปก็ก...       [SP]         1
2       [อังคณา กสม. โพสต์ระบุเตรียมเข้าร้องต่อ ปอท.เร...       [SP]         1
3       [รองผู้ว่าราชการจังหวัดภูเก็ตลงพื้นที่ตรวจสอบเ...       [SP]         1
4       [อันโตนิโอ คอนเต สร้างปรากฏการณ์ให้กับทัพ งูให...       [SP]         1
...                                                   ...        ...       ...
370132  [กึ้ง เฉลิมชัย แจงไปทำบุญที่เมียนมา ไปกันหลายค...       [SP]         1
370133  [จอร์จินิโอ ไวจ์นัลดุม มิดฟิลด์ทีมลิเวอร์พูล อ...       [SP]         1
370134  [เคน ภูภูมิ ไม่เสียเซลฟ์คนทักหน้าเปลี่ยน คาดอา...       [SP]         1
370135  [กรมอุตุนิยมวิทยา ประกาศ ฉ.16 พายุดีเปรสชันคีโ...       [SP]         1
370136  [ชาวบ้านบางเทากลับมาใช้ชีวิตตามปกติ หลังปลดล็อ...       [SP]         1

[370137 rows x 3 columns] (11000, 3) (11000, 3)
(37

เปลี่ยน Dataframe เป็น dictionary เพื่อหลีกเลี่ยง  pyarrow error

In [12]:
train = train_df[["tokens","conn_label"]].to_dict(orient="series")
dev = dev_df[["tokens","conn_label"]].to_dict(orient="series")
test = test_df[["tokens","conn_label"]].to_dict(orient="series")

กำหนด features ของ Dataset โดยใช้คำสั่ง` Features`
เนื่องจาก ข้อมูลของเราเป็น sequence ของ tokens จึงกำหนดให้


*   column `tokens` เป็น sequence ของ string
*   column `conn_label` เป็น sequence ของ `Classlabel`

ในที่นี้ column `conn_label` จะเป็น sequence ของ Label ['CON','N']
เช่น ` ['N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N'] `หรือ `['N', 'N', 'N', 'N','N', 'N', 'N', 'CON', 'N']`






In [13]:

conn_label = ['CON', 'N', 'SP']

conn_features = Features({
    "tokens": Sequence(Value('string')),  # Sequence of strings for tokens
    "conn_label": Sequence(feature=ClassLabel(names=conn_label))  # Sequence of class labels
})

ใช้คำสั่ง `DatasetDict` เพื่อเก็บข้อมูลเป็น dictionary ของ dataset



In [14]:
data = DatasetDict({'train': Dataset.from_dict(train,features=conn_features),
                 'dev': Dataset.from_dict(dev,features=conn_features),
                 'test': Dataset.from_dict(test,features=conn_features)})

ลองดู features ที่กำหนดไว้

In [15]:
data['train'].features

{'tokens': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None),
 'conn_label': Sequence(feature=ClassLabel(names=['CON', 'N', 'SP'], id=None), length=-1, id=None)}

## Preprocessing the data

`tokenizer` ของ BERT จะเปลี่ยนข้อมูลจาก list of tokens ให้กลายเป็น input_ids และ attention _mask สำหรับโมเดล
ใช้คำสั่ง `is_split_into_words=True` ถ้าเราใช้ข้อมูลที่ตัดแบ่งคำมาเรียบร้อยแล้ว

In [16]:
tokenizer(['คนร้าย', 'ซุก', 'ระเบิด'],truncation=True, is_split_into_words=True)

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


{'input_ids': [5, 10, 1343, 10, 6068, 10, 926, 6], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1]}

ตัวอย่างการ tokenized ประโยค `['คนร้าย', 'ซุก', 'ระเบิด', 'ใน', 'รถ', 'จักรยานยนต์', 'ก่อน', 'จุด', 'ชนวน']`

In [17]:
example = data['test']
print(example["tokens"])

[['มีชัย ไม่ยี่หระเสียงค้านชงสูตรพิสดารเลือกตั้ง ส.ส. ประกาศ ผลช้าไปชั่วโมงสองชั่วโมงไม่เห็นเป็นไร แสลงหูชื่อ สมชัย ชิ่งหนีดื้อๆ พรเพชร ให้นายกฯ ตัดสินใจปลดล็อกพรรคการเมือง'], ['กีเก ซานเชซ ฟลอเรส  กุนซือเลือดกระทิงของทีมวัตฟอร์ด  เมินประเด็นจุดโทษปัญหาในเกมพรีเมียร์ลีก อังกฤษ นัดที่แตนอาละวาดเปิดบ้านพ่าย คริสตัล พาเลซ 0-1ชี้ทีมของเขาเล่นไม่ดีพอเอง'], ['เนปาลระทึก หลังเกิดพายุฝนฟ้าคะนองถล่มทางใต้ สร้างความเสียหายหลายหมู่บ้าน เบื้องต้นพบผู้เสียชีวิตแล้ว 30 ศพ บาดเจ็บ 400 ราย ระบบสาธารณูปโภคพังพินาศ'], ['เป็นศูนย์รวมของความคิดสร้างสรรค์และคอมมูนิตี้คนรุ่นใหม่ ล่าสุด อุสรา ยงปิยะกุล คว้าศิลปินไทยรุ่นใหม่จากนิวยอร์ก กันตภณ เมธีกุล มาร่วมคอลลาโบเรชั่น สินค้าลิมิเต็ด อิดิชั่น  ODS X GONGKAN'], ['สหประชาชาติประเมินว่า สังคมเมียนมากำลังก้าวเข้าสู่สังคมผู้สูงอายุ ประชากรเมียนมากว่า 9% มีอายุมากกว่า 65 ปีขึ้นไป เเละจะเพิ่มสูงขึ้นเป็น 25% ภายในปี 2050บ้านตะวันลับ Twilight Villa ถูกจัดตั้งขึ้นในปี 2010 เพื่อแก้ไขปัญหาผู้สูงอายุที่ถูกทอดทิ้งเพิ่มมากขึ้นในสังคมเมียนมา ปัจจุบันมีผู้พักอาศัยอยู่ในบ้าน

In [18]:
tokenized_input = tokenizer(example["tokens"], is_split_into_words=True)
print(tokenized_input)

{'input_ids': [[5, 10, 11985, 729, 7511, 327, 872, 236, 6698, 4833, 1979, 24281, 216, 10, 40, 11, 40, 11, 10, 476, 10230, 17942, 797, 291, 797, 1394, 12360, 10, 5967, 154, 1439, 237, 10, 18582, 10, 16493, 981, 6130, 34, 10, 660, 1356, 10, 21, 1193, 10, 643, 11173, 218, 144, 6], [5, 10, 2389, 1261, 10, 2269, 2148, 666, 10, 20701, 7225, 10, 4344, 1040, 10660, 3537, 6724, 5769, 10, 12173, 747, 9549, 348, 3414, 660, 3594, 10, 943, 10, 6933, 18171, 19213, 6764, 7348, 10, 12931, 10, 20495, 10, 13923, 1119, 230, 511, 200, 21818, 185, 6], [5, 10, 8987, 10020, 10, 14285, 2802, 6103, 3563, 10876, 10, 954, 779, 414, 1123, 14090, 13441, 308, 22, 10, 313, 10, 1034, 10, 1698, 10, 2945, 10, 437, 13276, 40, 15016, 2011, 15345, 6], [5, 10, 17, 19929, 16, 1082, 2618, 13, 2144, 11241, 17321, 6622, 8309, 10, 9160, 104, 9, 10, 4115, 8153, 1403, 10, 2564, 2143, 109, 4361, 32, 4931, 10, 67, 46, 825, 307, 10, 14616, 1403, 10, 3176, 4856, 169, 9, 1702, 852, 2970, 10, 399, 1332, 396, 10281, 120, 8712, 808, 2970

สามารถดูได้ว่า BERT ตัดคำใหม่ออกมาเป็นอย่างไร โดยใช้คำสั่ง `tokenizer.convert_ids_to_tokens(input_id)`

In [19]:
tokenizer.convert_ids_to_tokens(100)

'ต่อ'

In [20]:
[tokenizer.convert_ids_to_tokens(x) for x in tokenized_input["input_ids"] ]

[['<s>',
  '▁',
  'มีชัย',
  '▁ไม่',
  'ยี่',
  'ห',
  'ระ',
  'เสียง',
  'ค้าน',
  'ชง',
  'สูตร',
  'พิสดาร',
  'เลือกตั้ง',
  '▁',
  'ส',
  '.',
  'ส',
  '.',
  '▁',
  'ประกาศ',
  '▁ผล',
  'ช้าไป',
  'ชั่วโมง',
  'สอง',
  'ชั่วโมง',
  'ไม่เห็น',
  'เป็นไร',
  '▁',
  'แส',
  'ลง',
  'หู',
  'ชื่อ',
  '▁',
  'สมชัย',
  '▁',
  'ชิ่ง',
  'หนี',
  'ดื้อ',
  'ๆ',
  '▁',
  'พร',
  'เพชร',
  '▁',
  'ให้',
  'นายกฯ',
  '▁',
  'ตัดสินใจ',
  'ปลดล็อก',
  'พรรค',
  'การเมือง',
  '</s>'],
 ['<s>',
  '▁',
  'กี',
  'เก',
  '▁',
  'ซาน',
  'เช',
  'ซ',
  '▁',
  'ฟลอ',
  'เรส',
  '▁',
  'กุนซือ',
  'เลือด',
  'กระทิง',
  'ของทีม',
  'วัต',
  'ฟอร์ด',
  '▁',
  'เมิน',
  'ประเด็น',
  'จุดโทษ',
  'ปัญหา',
  'ในเกม',
  'พร',
  'ีเมียร์ลีก',
  '▁',
  'อังกฤษ',
  '▁',
  'นัดที่',
  'แตน',
  'อาละวาด',
  'เปิดบ้าน',
  'พ่าย',
  '▁',
  'คริสตัล',
  '▁',
  'พาเลซ',
  '▁',
  '0-1',
  'ชี้',
  'ทีม',
  'ของเขา',
  'เล่น',
  'ไม่ดีพอ',
  'เอง',
  '</s>'],
 ['<s>',
  '▁',
  'เนปาล',
  'ระทึก',
  '▁',
  'หลังเกิ

จะเห็นได้ว่า BERT เพิ่ม  `'▁'` เข้าไปเป็น word boundary และตัดคำบางคำออกเป็นคำย่อยๆ เช่น  `'จักรยานยนต์'` กลายเป็น  ` '▁จ',
 'ักรยานยนต์'`

ซึ่งกลายเป็นปัญหาเนื่องจาก sequence label ต้นฉบับของเรามีแค่ 9 labels  แต่ tokens จาก BERT มีถึง 20 tokens






In [21]:
len(example["conn_label"]), len(tokenized_input["input_ids"])

(11000, 11000)

ปัญหานี้แก้ได้โดยใช้ `word_ids` ที่ออกมาพร้อมกับ `tokenized_input`




In [22]:
print(tokenized_input.word_ids())

[None, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, None]


`tokenized_input.word_ids()` จะบอกเราว่า token จาก BERT มาจากคำที่เท่าไหร่ในประโยค ส่วน special token เช่น `<s>` จะ return ค่า None

เราจึงกำหนดให้ label ของ  special token เป็น -100 ซึ่งเป็นค่าที่จะถูก ignore ในขั้นตอน training
และกำหนดให้ subword ย่อย ทุกอันที่มาจากคำเดียวกัน มี label เดียวกัน

In [23]:
word_ids = tokenized_input.word_ids()
aligned_labels = [-100 if i is None else example["conn_label"][i] for i in word_ids]
aligned_labels

[-100,
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 [2],
 -100]

In [24]:
len(aligned_labels), len(tokenized_input["input_ids"])

(51, 11000)

วิธีการ map label นั้นมีสองแบบคือ


1.   Label ทุก subword ให้เหมือนกัน
2.   Label เฉพาะ subword token แรก และให้ subword ที่เหลือ เป็น -100

โดยในตัวอย่างนี้เราจะใช้วิธีแรก



In [25]:
label_all_tokens = True
#True: all tokens have same label as original word
#False: only the first token have same label as original word

In [26]:
def tokenize_and_align_labels(examples):
    tokenized_inputs = tokenizer(examples["tokens"], truncation=True, is_split_into_words=True)
    tokens = [tokenizer.convert_ids_to_tokens(x) for x in tokenized_inputs["input_ids"] ]
    ids=[]
    labels = []
    for i, label in enumerate(examples["conn_label"]):
        word_ids = tokenized_inputs.word_ids(batch_index=i)
        previous_word_idx = None
        label_ids = []
        for word_idx in word_ids:
            # Special tokens have a word id that is None. We set the label to -100 so they are automatically ignored in the loss function.
            if word_idx is None:
                label_ids.append(-100)
            # Set the label for the first token of each word.
            elif word_idx != previous_word_idx:
                label_ids.append(label[word_idx])
            # For the other tokens in a word, we set the label to either the current label or -100, depending on
            # the label_all_tokens flag.
            else:
                label_ids.append(label[word_idx] if label_all_tokens else -100)
            previous_word_idx = word_idx

        labels.append(label_ids)
        ids.append(word_ids)

    tokenized_inputs["labels"] = labels
    tokenized_inputs["word_ids"] = ids
    tokenized_inputs["tokens_bert"] = tokens
    return tokenized_inputs


In [ ]:
tokenized_datasets = data.map(tokenize_and_align_labels, batched=True)

Map:   0%|          | 0/370137 [00:00<?, ? examples/s]

## Fine-tuning the model

In [ ]:
label_list = data['train'].features["conn_label"].feature.names

In [ ]:
label_list

In [ ]:
model = AutoModelForTokenClassification.from_pretrained(lm_name, num_labels=len(label_list))
model_name = model_checkpoint.split("/")[-1]

run_name = f"{model_name}-{num_epoch}epoch-{condition}"

args = TrainingArguments(
    output_dir=f"discon_model/{model_name}-{num_epoch}epoch-{condition}",
    run_name=run_name,  # Explicitly set the run name
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=num_epoch,
    save_strategy=save,
    save_total_limit=2,
    remove_unused_columns=False,
    weight_decay=0.01,
    push_to_hub=True,
)
data_collator = DataCollatorForTokenClassification(tokenizer)
metric = load("seqeval")

In [ ]:
def compute_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    # Remove ignored index (special tokens)
    true_predictions = [
        [label_list[p] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]
    true_labels = [
        [label_list[l] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]

    results = metric.compute(predictions=true_predictions, references=true_labels)
    return {
        "precision": results["overall_precision"],
        "recall": results["overall_recall"],
        "f1": results["overall_f1"],
        "accuracy": results["overall_accuracy"],
    }

In [ ]:
trainer = Trainer(
    model,
    args,
    train_dataset=tokenized_datasets['train'],
    eval_dataset=tokenized_datasets['dev'],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [ ]:
trainer.train(resume_from_checkpoint="your-model/checkpoint-1000")

##Evaluation for gold standard Pretokenized Dataset

In [ ]:
predictions, labels, _ = trainer.predict(tokenized_datasets['test'])
predictions = np.argmax(predictions, axis=2)

In [ ]:
bert_prediction = [
    [(id, token, prediction) for (id, token, prediction) in zip(row_id, row_token,row_predictions) ]
    for row_id, row_token, row_predictions in zip(tokenized_datasets['test']['word_ids'],tokenized_datasets['test']['tokens_bert'],predictions)
]

gold_label = [
    [label for label in row_label ]
    for row_label in tokenized_datasets['test']['conn_label']
]

ลองดู ผล prediction จาก  BERT

In [ ]:
bert_prediction[13]

In [ ]:
len(bert_prediction[13])

เทียบกับ Label ที่ถูกต้อง

In [ ]:
gold_label[13],len(gold_label[13])

In [ ]:
print(
    [(token, label) for (token, label) in zip(tokenized_datasets['test']['tokens'][13],gold_label[13])]
    )

In [ ]:
wrap_predict = []
for row in bert_prediction:
    predict_row=[]
    previous_word=None
    for item in row:
        if(item[0] is not None):
            #skip special token
            if(item[0] !=previous_word):
                predict_row.append(item[-1])
                previous_word = item[0]
    wrap_predict.append(predict_row)

In [ ]:
print(
    [(token, label) for (token, label) in zip(tokenized_datasets['test']['tokens'][13],wrap_predict[13])]
    )

In [ ]:
def flatten(t):
    return [conn_label[item] for sublist in t for item in sublist]
flat_true_predictions = flatten(wrap_predict)
flat_true_labels = flatten(gold_label)

In [ ]:
result = classification_report(flat_true_labels,flat_true_predictions,output_dict=True,labels=conn_label)
result_df=pd.DataFrame(result).transpose()
result_df